In [2]:
!nvidia-smi

Thu Apr 30 02:10:41 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 410.72       Driver Version: 410.72       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:2D:00.0 Off |                    0 |
| N/A   35C    P0    31W / 250W |   2278MiB / 16280MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
|   1  Tesla P100-PCIE...  Off  | 00000000:31:00.0 Off |                    0 |
| N/A   31C    P0    31W / 250W |   6025MiB / 16280MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
|   2  T

In [3]:
%env NVIDIA_VISIBLE_DEVICES 0,1,2,6,7
%env CUDA_VISIBLE_DEVICES 0,1,2,6,7

env: NVIDIA_VISIBLE_DEVICES=0,1,2,6,7
env: CUDA_VISIBLE_DEVICES=0,1,2,6,7


In [4]:
import os
from io import StringIO
from collections import defaultdict
import json

import pandas as pd
from tqdm import tqdm
import IPython

import numpy as np

%matplotlib inline
from matplotlib import pyplot as plt

import pickle

In [5]:
cxt = []
with open('data/NCPPolicies_context_20200301.csv', 'r', encoding='utf-8') as f:
    for line in f:
        cxt.append(line.replace('\t', '|!', 1))
cxt = '\n'.join(cxt)
df_cxt_all = pd.read_csv(StringIO(cxt), delimiter='\|!', error_bad_lines=False)
df_cxt = df_cxt_all.set_index('docid')
df_cxt

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:6: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  


text
docid                                                                              
edd1413c78e534afb136f36fdc9c9a00  福建：6部门联合出台暖企措施支持复工稳岗 为解决企业复产的用工困难，经省政府同意，省人社厅、...
230b6fc2a40937f9adf45ea97abad846  化龙桥站至李家坪站区间隧道贯通 12月30日，施工人员在重庆轨道交通九号线一期工程化龙桥站至...
8bab952dfa1a367da1b8e7ad864d766b  吉林多措并举保民生  2月18日，省政府新闻办围绕就业和医疗保障等民生问题召开新闻发布会。省...
ccc5129a465d312b9528b0b04aa4399e  山西加快推进口罩生产供应 新冠肺炎疫情发生后，我省积极督促企业扩产、转产、增产医疗防护物资。...
eb04c2ada51a3161b8477de607721c64  广东：暖企添动力 扩产有信心 2月18日，位于番禺汽车城的广汽新能源，机器人不断挥舞着手臂，...
901e0896408237b398cf13543170fd7b  青海加快信息化建设 支撑“放管服”改革 近日，我省开展了市场监管系统市场主体登记数据质量建设...
a84ad5c0fc7d3755926ec5bf2b2d9dae  重庆出台援企稳岗返还政策 2月16日，记者从市人力社保局获悉，为切实减轻中小企业负担，充分发...
a4c5052b84643fcba77ba4fd2e8da811  云南：各地积极组织企业复工复产 连日来，我省各地在确保疫情防控措施到位的基础上，积极组织当地...
976af8941a4e3e218a31e98fa76a42b8  辽宁智慧助力科技战“疫” 紧急启动两批攻关项目，多项科研工作取得进展 辽宁智慧助力科技战“疫...
319e33a428ba3f83aa410b1bacbce7c7  河北：全力保障食盐、农资、居民生活必需品供应 省供销社充分发挥组织体系和经营服务网络优势 全...
99ad086e719539ed98a662ecf391f10f  安徽支持省属企业打好疫情防控阻击战 记者日前从省国资委获悉，为鼓励支持广大省属企业在疫情防控...
f5c83eb87f183083a4957555b05c4ead  吉林省公安户政部门：推出系列 为积极应对新冠肺炎疫情，1月24日以来，全省户政管理部门和公安...
04c987b9bd5e30e88615c69957ead487  浙江：全省各地“健康码”陆续上线 以大数据赋能精密智控。连日来，“健康码”正在我省各地推广，...
5ee6d93bd42a3fda9be81c481a23a8a1  关于深入优化京津口岸营商环境进一步促进跨境贸易便利化若干措施的公告 关于深入优化京津口岸营商...
4f0239d5d8fb33558770d6a042d5b391  浙江率先实现健康码全覆盖 杭州在全国率先推出健康码之后，这一通行方式被迅速扩展到全省。截至2...
3fd6b4506e703694a3996e52a6efad2b  山西省建立疫情防控建设项目环评审批“绿色通道” 近日，省生态环境厅出台《关于切实做好疫情防控...
7ba5e0638f3f3cbfb4ce9efae778db71  福建：七举措推行“不见面”审批 省发改委日前下发通知，提出七条举措做好疫情防控期间投资项目远...
f0d16de6d41d3f8dad97dcf77cce0155  河北2座水电站成为国家绿色小水电示范电站 河北2座水电站成为国家绿色小水电示范电站 至此，全...
688c8957fdbc3f54a9b34285a6936ee3  吉林“互联网+公安”综合服务平台推出新冠肺炎密切接触者线上检测 为积极应对和阻击新冠肺炎疫情...
b00e2026d2dd39de8af5440efce30e31  关于拟批准成立北京市通州区德道职业技能培训学校的公示 依据《中华人民共和国民办教育促进法》、...
acaf2964128a3d308243f25cd23e7318  关于延期使用部分小客车指标的通告     根据目前本市新型冠状病毒疫情防控和市民生产、生活实...
ed79c0f55bac3aa9aee9c09b6d3b4f19  关于第六次北京市农业产业化重点龙头企业 认定合格名单的公示 各有关单位： 　　根据《北京市农...
968e79715f483305972b817e6e2aff93  北京市市场监督管理局关于在疫情防控期间提倡网上办理登记注册事项的倡议书 为全面加强疫情防控，...
68656e2c579634f6b59b831b1667c288  湖北省为企业防疫提供法律服务指引 企业能否向社会公众募集慈善资金，是否必须通过慈善组织？在延...
3285f224b22c38c483faa0911bfd86b8  黄河水利委员会全力做好黄河下游春灌供水工作 目前，正处在新冠肺炎疫情防控关键时期，也正值黄河...
8e006dc77cda3b639e6a6b3a86e02466  关于购买第三方服务协助开展第七次全国人口普查区域划分工作的通知 北京市丰台区统计局关于购买第...
082105b260e63b6197145a6ec8c9f15b  关于公布2019年北京市应急管理领域 各区应急管理局、人力资源和社会保障局、教育委员会，各相...
a47a0e211f0e3c0994649cdefe2e47c8  关于二〇一九年二季度北京市通州区登记失业人员参加职业培训期间生活补贴资金的批复 你学校关于《...
de3686ac6e27362d90aa2bbc72bc07b4  国务院联防联控机制2月17日新闻发布会预告 2020年2月17日新闻发布会预告 国务院联防联...
1ba18f69e9663f3f9dc625b5a7483b76  北京：小客车调控政策将完善优化 2020年北京市交通综合治理行动计划发布 小客车调控政策将完...
...                                                                             ...
2f1d07cabe6b3c89bb7575d6cf306e1b  四川省应对新型冠状病毒肺炎 疫情应急指挥部公告 （第11号） 四川省应对新型冠状病毒肺炎 疫...
bc2e70024a203ca0a343825145ddb703  国家税务总局关于开展2020年“便民办税春风行动”的意见 【发文单位】 国家税务总局 【发布...
a9f87fa0e85d3bc3bc6d7d5eac82c230  2019年度绍兴市市场监督管理局滨海新城分局企业年报提示性公告 绍兴绍泽电子科技有限公司等2...
f96b8f519b94345d9c59d15a97f9a795  2019年12月份及2020年元旦春节食品安全抽样检测情况通报 2019年12月份及2020...
06a73a0ee1c83169b7f1b275640cceb3  虞山街道第三批房屋征收搬迁清零扫尾“百日攻坚”行动圆满收官 日前，方塔街13号地块剩馀的1户...
c430472ef62538a29db9c5e94b249140  山东省人民政府 政策解读 部门解读｜《关于积极应对新冠肺炎疫情加快恢复农业生产 确保重要农产...
a1a93c4f046a37cb9e2d734bca7da0e0  江西省新型冠状病毒感染的肺炎疫情防控应急指挥部令 各市、县（区）人民政府、赣江新区管委会，省...
0424781a80223074b572dca0b019b970  国家税务总局福建省税务局关于防范新型冠状病毒传播的办税提示 尊敬的纳税人、缴费人： 近期，全...
0045268c16353544aa50fba63fac2581  关于授权南充市政府国有资产监督管理委员会履行企业出资人职责的通知 月底前全面完成企业移交工作...
843a9c35d49a3222868533048b06504c  山东省人民政府 政策文件 山东省人民政府关于任免侯成君等工作人员职务的通知 山东省人民政府 ...
b7cfd7b49f9d3a68b2d1551b1955b2ec  山东省人民政府 政策文件 山东省人民政府关于任免张成伟等工作人员职务的通知 山东省人民政府 ...
325221a2c2b6304bb241cfb7cabc65fc  四川省应对新型冠状病毒肺炎疫情应急指挥部 四川省应对新型冠状病毒肺炎疫情应急指挥部 关于做好...
e66bc263792030479c7513be56d62175  四川省应对新型冠状病毒肺炎疫情应急指挥部 四川省应对新型冠状病毒肺炎疫情应急指挥部 关于做好...
4164391b33063f72bc697dc1feea804c  四川省应对新型冠状病毒肺炎疫情应急指挥部 四川省应对新型冠状病毒肺炎疫情应急指挥部 关于做好...
dc043e7b957a39878522948e546cfcd0  国家税务总局关于优化纳税缴费服务配合做好新型冠状病毒感染肺炎疫情防控工作的通知 税总函〔20...
f74fa92851643dc49b18ec148699a8ee  银行密集发行防疫专项同业存

In [6]:
df_test = pd.read_csv('data/NCPPolicies_test.csv', delimiter='\t')
df_test

id  \
0     0ce5c44a54d63a5b9b7c9657d1919fc7   
1     0e72999704f430d8aa5f1233d71bf0cb   
2     0f17f97f38fb3174ab58acda1f1c3ff7   
3     c0c35634fdb83a40884fadebb0e82ff7   
4     0caca9df37d5388f97ef351eb98cc58a   
5     bd0e4148938333729e152ed01bf2640f   
6     0d335cafbf3a33dc924f17bfd2cb6383   
7     e0f54daebfb73bb690f3f0274b8fc843   
8     f0c4109f95af38929cf38cf4411eac1a   
9     0f9250b1ff9f32a28189ffdfc62a2dc9   
10    0d6e16a184213fa68c6790e5dd0f9813   
11    e0b69a64858733da86412649339d958f   
12    0e96ea5396e7377389a88f6233ea8037   
13    0ad2d8b939163fbfb8d73c2fa64cb714   
14    ece0f74dad3933f0af1fdf19a64ac023   
15    0f5d9ade51123aecba1aaab3d92bad5d   
16    0d3d1f021b0731dab01805c73a3866b2   
17    d0e18aba42453538995aeed8ba11bcb0   
18    c0af116827c537428b976cd529dcfd92   
19    ba0c4dc88ed43ef5a6f9303fd5d17a78   
20    0b9fedc8da9d3aed8da3aa6894a5d4fd   
21    0ff281d0409c30c1b6744b2eb5cf4723   
22    d0f4a969eaec340a819035cb21f8dc11   
23    ae0c442fb44c3cfbb61386b3a429e43d   
24    0c315f7a1ea2357fa677196d9a6e9743   
25    0f2b4ceb316a336996a8544ba031bc68   
26    c0ae20ab25193b5d8dd3d53cbe2c85a2   
27    b0e3aa5637d533f084f2cc4e3df76625   
28    0c24f4d4aea8327aac47ea8a58ca3568   
29    00ffb393d0063cb39bfc7e63c46cf65a   
...                                ...   
1613  df6e9628423a355389aecfac9964a357   
1614  8e550193c0553da3812f8c1094ce1dbb   
1615  8e9586cf6dbb357190ca48d82f5b82e9   
1616  905308493e6039d990544d133ff0078d   
1617  de4e01039cae3e66adb51a0e869e4088   
1618  7645e72003023b99a4c182758d8be335   
1619  cf053210911e381eaec5a9bdb6cf6241   
1620  7e1498ce386c341db5b39ac31987d705   
1621  c209e590ab11318eaa4f0120ebe5262f   
1622  39784431029e332bb0fb7d22d2c87cd5   
1623  5764898e00853fef9c9c7a02047f0879   
1624  c31e0646cfcb3b3aa82ac20026b3b49d   
1625  dd8e9031ab213335a6b37c460dcb7e56   
1626  d32e545b75433148acf805f0fd2998b5   
1627  d462e794ace93c1abb03a38d33fcdee0   
1628  e3e43946a5de332d83f97c771d61b449   
1629  a5819e96760c3e868511402e23b66757   
1630  d5e6242ff42a385693187076e3adc8b4   
1631  f983e74766a63b2a9ba35d31ec81f12e   
1632  aa2e9620db51393aafff7854fde7980d   
1633  91e463fdb97433a39d274dba98dbb5ee   
1634  cfe211111e563191973fe9a5bac146f0   
1635  2e103113ffe73292a4e35190071d32f5   
1636  1e92666267e130109e54823f0f67487f   
1637  2e90619a772439588a975e9078d35aa0   
1638  53e0719047fc3326963a10a48bd924d4   
1639  a27e530350ed33438a34f675f0fc461a   
1640  e4e75261297f3a49b0b7679920ba68a8   
1641  345641e320da302b8b5e39cdb2b003a9   
1642  be906e22443a37bca5f4db6ba461d899   

                                               question  
0                            天津市继续教育网在“抗疫知识专栏”中设有哪两类课程？  
1                                   北京市提供的优惠政策针对哪些重点企业？  
2                                  泉州市对举报违规餐饮店的举报人有何奖励？  
3                          为保证疫情期间食品供应，广州市多少家商户上了饿了吗平台？  
4                在北京市法律援助中心服务大厅开始对外提供法律咨询之前，如何获得法律咨询服务？  
5                         广州人力资源服务机构为五类企业成功介绍员工的给予多少补助？  
6                                 上海普陀区企业在哪里线上登记员工健康信息？  
7                           救助机构通过什么方式对于生活无着的流浪乞讨人员来救助？  
8                      截至2月4日，北京东城区向湖北十堰市郧阳区拨付多少财政援助资金？  
9                                      青海西宁平价供应的蔬菜有哪6种？  
10                                 四川对居民个人提出了哪些要求来防控疫情？  
11                          福州市政府为福州市重点企业稳定生产开通了哪些绿色通道？  
12                                       西安市如何健全服务联系机制？  
13                              交通运输部在《方案》中将哪些列为关键控制指标？  
14                              浙江如何保障生活保供类电商及快递企业正常运行？  
15                       安徽省在疫情防控期间新增就业岗位的小微企业给予什么政策支持？  
16                           上海防疫物资生产企业，符合条件的企业贷款利率是多少？  
17                               河南省通过哪些途径平抑生活必需品价格等问题？  
18    “创客北京2020”中小企业创新创业大赛中设立“疫情防控”专题赛参赛者通过网络进行注册报名，...  
19                       南昌市出台了哪些政策来支持疫情防控物资和生活必需品生产企业？  
20                                       浙江对企业复工时间有何要求？  
21                                      武汉市紧急征集了多少台出租车？  
22                                 新疆维吾尔自治区微信公众号捐赠如何操作？  
23                      兰州海关在哪里设立进口防控物资

In [7]:
from elasticsearch import Elasticsearch
from elasticsearch.helpers import bulk

es = Elasticsearch(['10.224.54.36'])

import pickle
addr = pickle.load(open('./addr_dict.p', 'rb'))

locs = []

for prov in addr['provinces']:
    dprov = addr[prov]
    locs.append(prov if len(dprov['alias']) == 0 else dprov['alias'][0])
    
    for city in dprov['cities']:
        dcity = dprov[city]
        locs.append(city if len(dcity['alias']) == 0 else dcity['alias'][0])
        
import re

loc_pattern = re.compile('|'.join(locs))

def get_locs(s):
    return list((set([f.group() for f in re.finditer(loc_pattern, s)])))

def search_with_loc(question, n):
    doc = {
                "size": n, 
                "query": {
                    "bool": {
                        "must": [
                            {
                                "match": {
                                    "text": {
                                        "query": question,
                                        "minimum_should_match": f"50%"
                                    }
                                },
                            }
                        ],
                                
                        "should": [
                            {
                                "match": {
                                    "locs": ' '.join(get_locs(question))
                                }
                            }
                        ]
                    }
                }
            }
    try:
        _searched = es.search(index='yqzw', doc_type='_doc', body=doc)
        answers = []
        for item in _searched['hits']['hits']:
            answers.append({
                'docid': item['_source']['docid'],
                'text': item['_source']['text'],
                'locs': item['_source']['locs'],
                'score': item['_score']
            }) 
        return answers

    except:
        traceback.print_exc()

In [8]:
tmp = []

for row in tqdm(df_test.itertuples(), total=len(df_test)):
    _df = pd.DataFrame(search_with_loc(row.question, 30))
    _df['question'] = row.question
#     _df['answer'] = row.answer
    _df['id'] = row.id
    tmp.append(_df)
    
df_test_search = pd.concat(tmp, axis=0)
df_test_search

100%|██████████| 1643/1643 [00:17<00:00, 95.44it/s] 


docid  \
0   34830ac2ef5d314fbad41f7beed484f4   
1   959a48cfc31c3ab4a106bfe11031c21d   
2   1207253ea6443a289ff35ea397e4e7e5   
3   37d462351f6c3b98960054c5f6b4a2aa   
4   2f427b6378fd39a98802c2f1e41f01c6   
5   ad817898819632928ce836485be315e6   
6   660af8ed344136dba5d5cc31ab5b5527   
7   81c38f8f00353db0a0ab4a95e00a2fb7   
8   a304474fb92f3163a0a4e594230d4c77   
9   c6998b4e8c0239b7add3119443bc8be1   
10  49ca724bce8338aca7b7ff13d08dc63e   
11  3f06ba877f4c38fc95c7cb42bb64a33a   
12  612d4d7e71aa32f9b0bfa07f7835ee64   
13  bc854affe61a380c976788dbd4e64a85   
14  a72ddd164f443e6cb35ea727d327204a   
15  7ac6f51d851330b68e330ee682ff7f41   
16  448c9768799e349293f55bd9eb6cb68d   
17  06dfab7fa717387b957cb504486d6674   
0   79f4770c7f1d34d497a0e15fe32fcbc9   
1   1d5709f94aee3fed863c5e6af8c09f3b   
2   4f335d8f1c4a342d81d885725a086cfc   
3   4b6937b2c6ed33aa8985746e137c0616   
4   3c92bd59d55732aeb97cb3c2d7d680ca   
5   df989b9c1b7d37fe85b541e456a34e6d   
6   7b70f10e52343a8d991e321aa81f9d3a   
7   dc39f3e191283d44a729245ea1300c51   
8   acb9fc2971153209b39eb0c88f018b14   
9   4f4c372c792539a1a11655893c94679b   
10  fa2b0432449733a7ad6b97b95785f2b9   
11  494870f49a083a26af645fdf8ad2780c   
..                               ...   
0   327e5da5c8eb357383f1cd86558a04a4   
1   2526501c0a3730c5992b6187e07cacdc   
2   53058dce03183d59a90b26344e6935f9   
3   a3b9dcb6bc1d3d679cfa16dc2592fc1d   
4   7ba5e0638f3f3cbfb4ce9efae778db71   
5   efb95aa84a30386a8de4ad0d00e8d010   
6   1b5ee4cff45433d6896be12ab43c2466   
7   303a5432b8b73f108f04134391d83d37   
8   25e08107db74372eb9567dcf6c8c6620   
9   c82874ede1983be9a806bf9cf6e7740f   
10  3137957623c239388da40105dd33afa6   
11  4630a2acb8203012bfc2c5aa370469b9   
12  902fe339528932e5ac0a77cdfd38d913   
13  c1f36416c7073b05a6c8261bf5a785b3   
14  46fea86e851737f1bfe83c0220eced98   
15  fdb6056fba6c3949ac3563f28d64408c   
16  41655c2eaf9236d7ae7ff37ddda46674   
17  3e71b492fc9d3aae8c15889fc9ec07ed   
18  d0a1aed8739933b4bb8fbc4910d2fd79   
19  e36145b86a553cc2903d0d4d784ef86c   
20  453c9731eba33c57b6e62da5b0d9c752   
21  c9fd50c3927531cea5d0b31812bf262f   
22  aeb6f9eea74c35378cb6733808e7d119   
23  758c90cf557f389d8b16002dabcaa2b8   
24  8dee76946e8c3e67bd6ab133a8c0b474   
25  b8be1d48f08b343487e729edb86a984f   
26  e1839395c2123804a605d06d33a52955   
27  ff7f8c247eff3bfdbb98528eb19cd6df   
28  05c9fc7155e53c8c8822848075b8c7ff   
29  fb26d19359fd3816aa58df730a30955a   

                                                 locs       score  \
0                                                [天津]  111.040270   
1                                            [河北, 天津]   44.436560   
2                                            [湖北, 天津]   38.273895   
3                                            [四平, 天津]   34.756560   
4                                            [湖北, 云南]   30.586746   
5                                            [南充, 四川]   24.704430   
6                                        [河北, 北京, 天津]   21.202497   
7               [新北, 唐山, 河北, 天津, 朝阳, 张家口, 河源, 廊坊, 北京]   18.867722   
8   [成都, 福建, 四川, 郑州, 常州, 安徽, 福州, 湖南, 辽宁, 沈阳, 合肥, 深...   18.328693   
9                                        [保定, 湖北, 广西]   15.096468   
10                           [武汉, 湖北, 乐山, 新疆, 上海, 岳阳]   14.911323   
11  [山东, 福建, 江西, 郑州, 四川, 安徽, 开封, 辽宁, 山西, 河南, 贵州, 重...   14.360466   
12                                           [新疆, 西藏]   12.152779   
13  [桂林, 钦州, 河池, 百色, 防城港, 湖北, 柳州, 梧州, 贺州, 广西, 来宾, ...   12.101517   
14                                           [南充, 四川]   11.271748   
15                           [新北, 朝阳, 北海, 台中, 廊坊, 北京]   10.001039   
16                           [新北, 朝阳, 北海, 台中, 廊坊, 北京]   10.001039   
17                                               [北京]    8.281095   
0                                    [湖北, 上海, 北京, 河北]   30.085630   
1                                        [陕西, 北京, 安康]   28.983690   
2                                            [湖北, 北京]   28.206892   
3                               

In [9]:
from transformers import pipeline, AutoModelForQuestionAnswering, BertTokenizer, AutoConfig
from question_answering_pipeline import QuestionAnsweringPipeline
import torch
import re

from apex import amp

In [9]:
# model = AutoModelForQuestionAnswering.from_pretrained('./models/albert-chinese-large-v8/checkpoint-7000/')
# tokenizer = BertTokenizer.from_pretrained('./models/albert-chinese-large-v8/checkpoint-7000/')
# # model, optimizer = amp.initialize(model.to(device='cuda'), None)

# pip = QuestionAnsweringPipeline(model=model, tokenizer=tokenizer, device=6)

In [10]:
# test_preds = pip(
#     question=df_test_search.question.tolist(),
#     context=df_test_search['text'].str.replace(r'\s+', ' ').str.strip().str.slice(stop=5000).tolist(), 
#     max_answer_len=250, max_seq_len=512, max_question_len=64, doc_stride=128, topk=20
# )

# pickle.dump(test_preds, open('tmp/test-preds-v8-30.p', 'wb'))

100%|██████████| 48780/48780 [1:20:13<00:00,  7.56it/s]


In [11]:
# test_preds

[[{'score': 0.904844266933047,
   'null_score': 5.85971810219564e-05,
   'start': 247,
   'end': 333,
   'answer': '程：“新冠肺炎防疫小课堂”主要发布有关新冠肺炎的科学知识，“防疫抗疫身心调节公益课堂”主要发布中国心理学会、清华大学等知名专家讲授的有关疫情防控期间心理健康调适方法和技巧。'},
  {'score': 0.9020179335693115,
   'null_score': 0.00011481679872188746,
   'start': 247,
   'end': 333,
   'answer': '程：“新冠肺炎防疫小课堂”主要发布有关新冠肺炎的科学知识，“防疫抗疫身心调节公益课堂”主要发布中国心理学会、清华大学等知名专家讲授的有关疫情防控期间心理健康调适方法和技巧。'},
  {'score': 0.07545465456517686,
   'null_score': 5.85971810219564e-05,
   'start': 247,
   'end': 333,
   'answer': '程：“新冠肺炎防疫小课堂”主要发布有关新冠肺炎的科学知识，“防疫抗疫身心调节公益课堂”主要发布中国心理学会、清华大学等知名专家讲授的有关疫情防控期间心理健康调适方法和技巧。'},
  {'score': 0.0720331610067646,
   'null_score': 0.00011481679872188746,
   'start': 247,
   'end': 333,
   'answer': '程：“新冠肺炎防疫小课堂”主要发布有关新冠肺炎的科学知识，“防疫抗疫身心调节公益课堂”主要发布中国心理学会、清华大学等知名专家讲授的有关疫情防控期间心理健康调适方法和技巧。'},
  {'score': 0.000780778495079841,
   'null_score': 5.85971810219564e-05,
   'start': 331,
   'end': 333,
   'answer': '巧。'},
  {'score': 0.000717926257140844,
   'null_

In [13]:
# pickle.dump(test_preds, open('tmp/test-preds-v8-30.p', 'wb'))

In [31]:
test_preds = pickle.load(open('tmp/test-preds-v8-30.p', 'rb'))

In [36]:
from rouge.rouge import Rouge
from difflib import SequenceMatcher
import copy
import re

import thulac
thu = thulac.thulac(seg_only=True, user_dict='user_dict.txt')

import sys
sys.setrecursionlimit(10000)

rouge = Rouge()

def spacify(s):
    return re.sub(r'\s+', ' ', ' '.join(list(s)))

def get_result(model_preds, df_search, a, b, c, w1, w2, w3, w4):
    model_preds = copy.deepcopy(model_preds)
    
    max_answer_len = 2500
    answers = []
    for i, p in enumerate(model_preds):
        cands = []
        min_null_score = 10000
        for j, d in enumerate(p):
            if d['answer'] == '':
                min_null_score = min(min_null_score, d['score'])
            else:
                d['score1'] = c * d['score'] + (1 - c) * (1 - d['null_score'])
            
                
#                 if len(d['answer']) < 2 or len(d['answer']) > max_answer_len:
#                     d['score1'] = max(0, d['score1'] - 0.1)
                cands.append(d)

        cands = sorted(cands, key=lambda x:x['score1'], reverse=True)
        
        s1 = cands[0]['score1'] if len(cands) > 0 else 0
        s2 = cands[1]['score1'] if len(cands) > 1 else 0
        s3 = cands[2]['score1'] if len(cands) > 2 else 0
        s4 = cands[3]['score1'] if len(cands) > 3 else 0
        
        score_context = w1 * s1 + w2 * s2 + w3 * s3 + w4 * s4

        best_answer = cands[0]['answer'].strip()

        if min_null_score > 1:
            min_null_score = 0
            
        if len(best_answer) < 3 or len(best_answer) > max_answer_len:
            score_context = score_context - 0.5
            
        answers.append((best_answer, min_null_score, score_context))
        
    df_preds = pd.DataFrame(answers, columns=['pred', 'null_prob', 'prob'])

    df_search_pred = pd.concat([df_search.reset_index(drop=True), df_preds], axis=1)
#         df_search_pred = df_search_pred[df_preds['null_prob'] < thres]

    df_search_pred['score_all'] = df_search_pred['score'] * (1 - a - b) / 100 + df_search_pred['prob'] * a + (1 - df_search_pred['null_prob']) * b

    df_pred_select = []
    for k, _df in df_search_pred.groupby('id'):
        df_pred_select.append(_df.sort_values('score_all', ascending=False).iloc[0])

    df_pred_select = pd.DataFrame(df_pred_select)

    answer_pred_refine = []
    for row in df_pred_select.itertuples():
        matches = [m for m in SequenceMatcher(a=row.text, b=row.pred).get_matching_blocks() if m.size > 0]
        refine = row.text[matches[0].a: matches[-1].a + matches[-1].size]
        
        old_refine = copy.copy(refine)
        
        refine = refine.strip('，').strip(':').strip('：').strip('（').strip('；').strip('、').strip()
        
        if re.sub(r'\s+', '', refine) != re.sub(r'\s+', '', row.pred):
            refine = row.pred
        
        if len(refine) > 5 and len(re.findall('[。，：]', refine[:4])) > 0:
            for f in re.finditer('[。，：、]', refine[:4]):
                refine = refine[f.span()[0] + 1:]
                break
                
            print('----截取开头标点----')
        
        
        if re.match(r'^[的].*', refine):
            refine = refine[1:]
            print('----去掉开头停用词----')
            
        if matches[0].a != 0:
            tmp = row.text[matches[0].a - 1: matches[-1].a + matches[-1].size]
            tw = [w[0] for w in thu.fast_cut(tmp)]
            rw = [w[0] for w in thu.fast_cut(refine)]
            
            if len(rw) > 0 and rw[0] != tw[0] and rw[0] in tw[0]: # 少了一个字
                print('----去掉开头不完整词语----')
                refine = tmp[len(tw[0]):]
                
#         if matches[-1].a + matches[-1].size < len(row.text):
#             tmp = row.text[matches[0].a: matches[-1].a + matches[-1].size + 1]
#             tw = [w[0] for w in thu.fast_cut(tmp)]
#             rw = [w[0] for w in thu.fast_cut(refine)]
#             if len(rw) > 0 and rw[-1] != tw[-1] and rw[-1] in tw[-1]:
#                 print('----去掉结尾不完整词语----')
#                 refine = tmp[: len(tmp) - len(tw[-1])]
                
        refine = refine.strip('，').strip(':').strip('：').strip('（').strip('；').strip('、').strip()
                
        if old_refine != refine:
            print('old:', old_refine)
            print('new:', refine)
            
        answer_pred_refine.append(refine)

    df_pred_select['answer_pred_refine'] = answer_pred_refine

    return df_pred_select

Model loaded succeed


In [37]:
df_pred_select = get_result(test_preds, df_test_search, 0.3, 0, 0, 1, 0, 0, 0)
df_pred_select

old: 对承租国有资产类经营用房的中小微企业，2020年2月免收房租，3—4月房租减半。对在疫情期间给予中小企业房租、标准化厂房租金、物业费用减免的县域工业集中区、小微企业创业创新基地、中小企业特色载体，省级中小企业发展专项资金给予不超过10万元的一次性奖补。支持省级以上科技企业孵化器、众创空间、大学科技园等孵化载体减免在孵企业的办公、实验、科研和生产用房的租金，从科技发展专项资金中，按照减免租金的10%给予补助。属地政府可采取适当方式给予补贴。（
new: 对承租国有资产类经营用房的中小微企业，2020年2月免收房租，3—4月房租减半。对在疫情期间给予中小企业房租、标准化厂房租金、物业费用减免的县域工业集中区、小微企业创业创新基地、中小企业特色载体，省级中小企业发展专项资金给予不超过10万元的一次性奖补。支持省级以上科技企业孵化器、众创空间、大学科技园等孵化载体减免在孵企业的办公、实验、科研和生产用房的租金，从科技发展专项资金中，按照减免租金的10%给予补助。属地政府可采取适当方式给予补贴。
----截取开头标点----
old: 点：一是通过群众喜闻乐见的各种形式宣传科学防控；二是通过宣传好人好事、提供各类人性化服务，传递社区温度，取得群众支持；三是全面掌握社情民意，妥善处置苗头性问题，及时引导正确舆论。
new: 一是通过群众喜闻乐见的各种形式宣传科学防控；二是通过宣传好人好事、提供各类人性化服务，传递社区温度，取得群众支持；三是全面掌握社情民意，妥善处置苗头性问题，及时引导正确舆论。
old: 对在疫情防控期间不能按期办理驾驶证审验换证、机动车检验等业务的，
new: 对在疫情防控期间不能按期办理驾驶证审验换证、机动车检验等业务的
----去掉开头停用词----
old: 的360家
new: 360家
old: 不加收税款滞纳金、
new: 不加收税款滞纳金
----去掉开头不完整词语----
old: 计2.36亿元；
new: 2.36亿元
----去掉开头不完整词语----
old: 计1.69亿元
new: 1.69亿元
old: 早发现、早报告、早隔离、早治疗，
new: 早发现、早报告、早隔离、早治疗
----去掉开头不完整词语----
old: 驻2名
new: 2名
----去掉开头不完整词语----
old: 逐人建立信息台账，为实施有

----截取开头标点----
old: 第一步，“拦”下人员和车辆；第二步，“查”人员和车辆通行证；第三步，“问”人员是谁，从哪里来、到哪里去；第四步，“测”体温；第五步，“记”进出人员和车辆基本信息。
new: “拦”下人员和车辆；第二步，“查”人员和车辆通行证；第三步，“问”人员是谁，从哪里来、到哪里去；第四步，“测”体温；第五步，“记”进出人员和车辆基本信息。
old: 符合类别的南昌市商贸物流企业、园区（中心）到注册地所属县、区商务主管部门申请，并提供书面申请报告，报告中按相关要求需明确具体办理通行证的车牌号、车辆行驶路线、驾驶员身份证复印件、生活居住地及健康信息等车辆、人员基本信息；
new: 符合类别的南昌市商贸物流企业、园区（中心）到注册地所属县、区商务主管部门申请，并提供书面申请报告，报告中按相关要求需明确具体办理通行证的车牌号、车辆行驶路线、驾驶员身份证复印件、生活居住地及健康信息等车辆、人员基本信息
old: 市人社部门通过系统数据筛查出符合申领稳岗返还待遇的企业，审核发放後通过发送短信、推送网上服务大厅的方式通知企业确认申领。企业也可以自行登录广西壮族自治区&ldquo;数字人社&rdquo;网上服务大厅进行申请。（
new: 市人社部门通过系统数据筛查出符合申领稳岗返还待遇的企业，审核发放後通过发送短信、推送网上服务大厅的方式通知企业确认申领。企业也可以自行登录广西壮族自治区&ldquo;数字人社&rdquo;网上服务大厅进行申请。
old: 市民基本生活、公共事务办理、公共场所设施等各个方面，
new: 市民基本生活、公共事务办理、公共场所设施等各个方面
old: 延长至2020年3月31日，
new: 延长至2020年3月31日
----去掉开头不完整词语----
old: 区一律以社区为单位实行封闭式防控管理。
new: 一律以社区为单位实行封闭式防控管理。
old: （一）生产应对疫情使用的医用防护服、隔离服、医用及具有防护作用的民用口罩、医用隔离眼罩/医用隔离面罩、新型冠状病毒检测试剂盒、负压救护车、消毒机、消杀用品、红外测温仪、智能监测检测系统和相关药品等重要医用物资生产企业； （二）生产上述物资所需要的重要原辅料生产企业、重要设备制造企业和相关配套企业； （三）工业领域生产重要生活必需品的骨干企业； （四）重要医疗物资收储企业；

old: 截至目前，已收到85家企业提出的资金需求74.5亿元，
new: 截至目前，已收到85家企业提出的资金需求74.5亿元
old: 加强蔬菜市场监测，
new: 加强蔬菜市场监测
old: 积极运用互联网+、大数据等信息技术助力疫情阻击战，减少线下诊疗压力和交叉感染风险，
new: 积极运用互联网+、大数据等信息技术助力疫情阻击战，减少线下诊疗压力和交叉感染风险
----去掉开头不完整词语----
old: 过“穗康”微信小程序
new: “穗康”微信小程序
----去掉开头不完整词语----
old: 定《甘泉堡经开区有序分类推进企业复工复产的工作安排》，
new: 《甘泉堡经开区有序分类推进企业复工复产的工作安排》
----去掉开头不完整词语----
old: 助300元
new: 300元
old: 对国家确定的疫情防控重点保障企业，2020年新增的企业贷款，中央财政已按人民银行再贷款利率50%给予贴息；对省确定的疫情防控重点保障企业，省财政按人民银行再贷款利率50%给予贴息，贴息期限不超过1年。（
new: 对国家确定的疫情防控重点保障企业，2020年新增的企业贷款，中央财政已按人民银行再贷款利率50%给予贴息；对省确定的疫情防控重点保障企业，省财政按人民银行再贷款利率50%给予贴息，贴息期限不超过1年。
old: 因疫情防控所需快速释放产能或改扩建生产线的药品、医疗器械、卫生防护等医用物品制造企业和粮食、食用油、肉类、蔬菜、蛋品、水产品、饲料等生活必需品加工企业，
new: 因疫情防控所需快速释放产能或改扩建生产线的药品、医疗器械、卫生防护等医用物品制造企业和粮食、食用油、肉类、蔬菜、蛋品、水产品、饲料等生活必需品加工企业
old: https://wsxf.xfb.beijing.gov.cn/wsxf/action/index.html；
new: https://wsxf.xfb.beijing.gov.cn/wsxf/action/index.html
old: 通过在线直播教学、网络点播教学、班级QQ群或微信群发送课後作业，并通过网络或者电话等方式，
new: 通过在线直播教学、网络点播教学、班级QQ群或微信群发送课後作业，并通过网络或者电话等方式
----去掉开头不完整词语----
old: 于2019年3月
new: 2019年3月


----去掉开头不完整词语----
old: 现22家
new: 22家
----去掉开头不完整词语----
old: 币1700万元。
new: 1700万元。
----去掉开头不完整词语----
old: 于2月10日
new: 2月10日
----截取开头标点----
old: 化。《国务院办公厅转发国家发展改革委关于深化公共资源交易平台整合共享指导意见的通知》（国办函〔2019〕41号）
new: 《国务院办公厅转发国家发展改革委关于深化公共资源交易平台整合共享指导意见的通知》（国办函〔2019〕41号）
old: 对符合条件的不裁员或少裁员的参保企业，返还其上年度实际缴纳失业保险费的50%。对符合条件的面临暂时性生产经营困难且恢复有望、坚持不裁员少裁员的参保企业，进行“经营困难且恢复有望企业稳岗返还”，返还标准可按6个月的当地月人均失业保险金和参保职工人数确定，或按6个月的企业及其职工应缴纳社会保险费50%的标准确定。政策执行期限按照国家规定执行。（
new: 对符合条件的不裁员或少裁员的参保企业，返还其上年度实际缴纳失业保险费的50%。对符合条件的面临暂时性生产经营困难且恢复有望、坚持不裁员少裁员的参保企业，进行“经营困难且恢复有望企业稳岗返还”，返还标准可按6个月的当地月人均失业保险金和参保职工人数确定，或按6个月的企业及其职工应缴纳社会保险费50%的标准确定。政策执行期限按照国家规定执行。
----去掉开头不完整词语----
old: 十条
new: 条
----去掉开头不完整词语----
old: 物12小时内使用专用密封车辆单独收集清运，并及时焚烧处置。
new: 12小时内使用专用密封车辆单独收集清运，并及时焚烧处置。
old: 全面撤消市内国道、省道、高速公路出入口设置的交通检查检疫站点，全面恢复省内班线、市县乡道路客运班线、包车客运、城市公交、出租车和客货运服务，尽快实现交通道路、村庄、居民区卡口“清障”，畅通人流、物流通道，
new: 全面撤消市内国道、省道、高速公路出入口设置的交通检查检疫站点，全面恢复省内班线、市县乡道路客运班线、包车客运、城市公交、出租车和客货运服务，尽快实现交通道路、村庄、居民区卡口“清障”，畅通人流、物流通道
----去掉开头不完整词语----
old: 情12366
new: 12366
----去掉开头不完整

new: 在50%以下
----去掉开头不完整词语----
old: 客3月31日前
new: 3月31日前
----截取开头标点----
old: 业，一是重要医用物资企业；二是生产重要医用物资的重要原辅材料生产企业、重要设备制造企业和相关配套企业；三是生产重要生活必需品的骨干企业；四是重要医用物资收储企业；五是为应对疫情提供相关信息、通信服务和服务系统的企业，还有承担相应物资运输、销售任务的企业。
new: 一是重要医用物资企业；二是生产重要医用物资的重要原辅材料生产企业、重要设备制造企业和相关配套企业；三是生产重要生活必需品的骨干企业；四是重要医用物资收储企业；五是为应对疫情提供相关信息、通信服务和服务系统的企业，还有承担相应物资运输、销售任务的企业。
old: 不需要任何抵押或担保，
new: 不需要任何抵押或担保
old: 立即报告党委政府或者疫情防控指挥部，及时协调解决，
new: 立即报告党委政府或者疫情防控指挥部，及时协调解决
old: （一）项目申报。项目申报单位按照隶属关系将申报材料报各区商务局、经开区商务金融局、市属国有企业集团和总部企业。 （二）项目审核。各区商务局、经开区商务金融局、市属国有企业集团和总部企业对申报项目进行初审，通过初审的项目汇总後报市商务局进行复审。 （三）项目评审。通过复审的项目，由第三方中介机构对项目实施和投资等情况进行综合评审。
new: 一）项目申报。项目申报单位按照隶属关系将申报材料报各区商务局、经开区商务金融局、市属国有企业集团和总部企业。 （二）项目审核。各区商务局、经开区商务金融局、市属国有企业集团和总部企业对申报项目进行初审，通过初审的项目汇总後报市商务局进行复审。 （三）项目评审。通过复审的项目，由第三方中介机构对项目实施和投资等情况进行综合评审。
old: 免征增值税；
new: 免征增值税
----去掉开头不完整词语----
old: 网（www.chinatax.gov.cn）
new: www.chinatax.gov.cn）
old: 纳税人），
new: 纳税人）
----去掉开头停用词----
old: 的28条
new: 28条
old: （1）金税盘版开票软件：“汇总上传”－“远程清卡”； （2）税控盘版开票软件：“上报汇总”－“反写”； （3）税务UKEY开票软件：“汇总上传”－“上

docid                                  locs  \
29740  2224dc162e2831f693b41749dd361b17                              [西安, 陕西]   
14687  7484916ce1363d7baad2b41728be8a6b                                    []   
27122  b9f92ea490ac34c382294a67fc43024a                                  [苏州]   
41197  d91e7aa2bcd6379e958d35b63c6bb593                                    []   
858    13a32c4a820a30f89540d3ed15da2df6                          [浙江, 杭州, 上海]   
47373  e54ea064692c322a88dca26d36410f3d                                  [深圳]   
35162  b384f427eb72310db60745c08bb12686                          [保定, 南昌, 江西]   
46773  0c2efdf494c038939e2391b69b9d2ad2                                  [新疆]   
3131   076b9477df8d3f4495ac50ca68703d49                                  [江西]   
46095  f4229f46579e368c93aeb06b8440b68f                                  [四川]   
19018  5be3646f60363f85ab4aec806cd3d1de                              [上海, 中山]   
41707  bdee45a53ac03acb93277c6431ff4d13                                  [深圳]   
19647  c496ec77dedb31f19e38d6da80e6db23                                  [北京]   
35498  0e97455c4c79349dbc96983c639a96ab      [山东, 湖北, 四川, 福建, 浙江, 广东, 江苏, 湖南]   
39250  7853beb615e63df28c5cb7de237070a2                                  [陕西]   
19947  0a866f9daec13f0097a45b96832f2270                                  [重庆]   
44624  ca58bad1152530a391ba75a2ced0b032                                  [上海]   
44118  098bd64fb7133f4fba1fcdf9666c77a5                                    []   
20756  ffb9f2f17b1638469d8f0da74d8cd97b                                  [重庆]   
6941   3ddd3c31cea239cab46bc878d89a515e                              [湖北, 北京]   
47643  d6dad601f24834be87d99f099bd2d5ac                                  [青海]   
7241   07d79ba619573c0daf2b2fbe4c391f72                          [湖北, 莆田, 福建]   
21241  313afaec8c7836459b027b1677bcf7e4                                  [南昌]   
21742  300fa5a32aea3e72a6a5215bdee8e169                                  [吉林]   
36276  bae67642451630519d80cf2e0b4f84f8                  [河南, 杭州, 浙江, 周口, 宁波]   
31330  4d21a725286538e3befa0944246ae9a2                                  [武汉]   
22031  27739569da43307a8c53f06381d17de1                                    []   
8841   c129c1bc387c312284c3ef61b551c432                                  [广东]   
45427  d19cb4f3188331ca8863298de5f5439b                  [武汉, 湖北, 杭州, 温州, 南充]   
46803  643be50820d63b999786f511dd33f60b                                  [重庆]   
...                                 ...                                   ...   
13637  d0c0f1abfa3b399f8b585885b7a56320                                [乌鲁木齐]   
19467  dfd4d824eb6f34d0befdfca60bf6eea5                                  [阿里]   
43171  cc494d94af2838c4821180043dfc46ce                                  [北京]   
8051   c03efb794f543787b2b8c7103db46289                          [浙江, 杭州, 温州]   
22876  5e09fad8206c382286e227db61176df7                              [武汉, 湖北]   
40147  b571723c3a863ee2b4929edf9b6c2ee8  [武汉, 湖北, 贵州, 云南, 海南, 广西, 广东, 深圳, 襄阳]   
44894  37e6b875b2eb329f9512f81eb7269d9b                  [淮南, 滁州, 蚌埠, 合肥, 安徽]   
13997  99ab0b82d45c31c9b68d2672fa7c6ec4                                  [上海]   
12459  e3d7a4a509313963a5556356c3211ad5                                  [北京]   
10968  50b2263fd9ca314ea783084c0e040970                          [武汉, 湖北, 上海]   
2261   83f280a4e3c23c5a9ba16aa38de7ff30                                  [武汉]   
37504  045570b1bbf635feb489741de1665e2b                                  [湖北]   
44376  416e692b55f5313dacf02dcb1740becc                                  [江苏]   
11049  7797fc8c83d53672b870883be2865a99                                  [北京]   
21959  1a90bb57654d3967ad597d3f1f58fc3f                                  [北京]   
47763  3ec02e6e7c1f30b199ab6831ec018742                          [武汉, 四川, 成都]   
45741  2a649ee675803cdd86b59a26e612150f                                  [上海]   
4902   6a5d5def3ff5340b8b45eab3c1b8a073                          

In [38]:
df_rst = df_pred_select[['id', 'docid', 'answer_pred_refine']]
df_rst.columns = ['id', 'docid', 'answer']
df_rst

id                             docid  \
29740  000237f617a835f89a525db97b3bdbff  2224dc162e2831f693b41749dd361b17   
14687  0008bd92faaf330796e28e7bbef388a5  7484916ce1363d7baad2b41728be8a6b   
27122  0086edef25b33cc48beace3b3b887a52  b9f92ea490ac34c382294a67fc43024a   
41197  0094268b34103f53893010e457d2fcfe  d91e7aa2bcd6379e958d35b63c6bb593   
858    00ffb393d0063cb39bfc7e63c46cf65a  13a32c4a820a30f89540d3ed15da2df6   
47373  0160549e64153e3e86d2953dd4ab63cc  e54ea064692c322a88dca26d36410f3d   
35162  01938b5e30fc3481b660ab9209cdb240  b384f427eb72310db60745c08bb12686   
46773  019e56e6c3d039e2aff57f0f621a01e3  0c2efdf494c038939e2391b69b9d2ad2   
3131   01f05ca6015c33b796bb6e1ebc15e199  076b9477df8d3f4495ac50ca68703d49   
46095  020e11ee430b345583457f5629f96577  f4229f46579e368c93aeb06b8440b68f   
19018  021ecdf2706b3b4d9c12c00dced55a6e  5be3646f60363f85ab4aec806cd3d1de   
41707  0251587de3873351a8816a61e61fdbde  bdee45a53ac03acb93277c6431ff4d13   
19647  028a7023c890327ebc685b36eef524fe  c496ec77dedb31f19e38d6da80e6db23   
35498  02918fce2ed63755b4ce0555bf4a55a7  0e97455c4c79349dbc96983c639a96ab   
39250  030729b0ea04330b867670c963bad9dd  7853beb615e63df28c5cb7de237070a2   
19947  030f5d407db639508b7ea1f756fe2d7b  0a866f9daec13f0097a45b96832f2270   
44624  031125e4a9e73aefbf1c94f97bf78e50  ca58bad1152530a391ba75a2ced0b032   
44118  031203174b013a1aabd6ddf8933e9cb2  098bd64fb7133f4fba1fcdf9666c77a5   
20756  037dc33234703e73bdbb8fe2440bf186  ffb9f2f17b1638469d8f0da74d8cd97b   
6941   03abf4e85dec3bf38afc0b9e3b908594  3ddd3c31cea239cab46bc878d89a515e   
47643  03e4303a12f03ce8a296384111f3181f  d6dad601f24834be87d99f099bd2d5ac   
7241   03f3e743b404398c906b1c1c266e6f2f  07d79ba619573c0daf2b2fbe4c391f72   
21241  042ead595c113727b74c40fdfb6959f3  313afaec8c7836459b027b1677bcf7e4   
21742  047bfd00300534ad9674f1d517ae759c  300fa5a32aea3e72a6a5215bdee8e169   
36276  04907b27c30b369ab01425da488bf9cf  bae67642451630519d80cf2e0b4f84f8   
31330  0498b00c98c033e2823a6e1af652c6ed  4d21a725286538e3befa0944246ae9a2   
22031  049f059d135039a2906457736c24181b  27739569da43307a8c53f06381d17de1   
8841   04c9a4489cb93f83968ad0ef7117e022  c129c1bc387c312284c3ef61b551c432   
45427  05643000604b31c58054586a2cc00c7c  d19cb4f3188331ca8863298de5f5439b   
46803  0565e59a52353afc893d5b1c10aea45c  643be50820d63b999786f511dd33f60b   
...                                 ...                               ...   
13637  fc08def045753a22b1f36e34ffda538a  d0c0f1abfa3b399f8b585885b7a56320   
19467  fc26cf92a1e13469b1ee47d4da637819  dfd4d824eb6f34d0befdfca60bf6eea5   
43171  fc3069982ab6302f9d3e0225839b3763  cc494d94af2838c4821180043dfc46ce   
8051   fc4ba4efcc8131349bb7a94ddb03f866  c03efb794f543787b2b8c7103db46289   
22876  fc54aede1fba35bb800e249761271c1c  5e09fad8206c382286e227db61176df7   
40147  fc61197fe6293e9e96f01e9784b40045  b571723c3a863ee2b4929edf9b6c2ee8   
44894  fc688390200a3ed7997ba1d4904cff3b  37e6b875b2eb329f9512f81eb7269d9b   
13997  fc8ffe739e813f1284a787fb65c9124d  99ab0b82d45c31c9b68d2672fa7c6ec4   
12459  fcb07ae9120b3256a7e81323c5c7726c  e3d7a4a509313963a5556356c3211ad5   
10968  fcfe6cc495f136748baf6008ba3f6e4a  50b2263fd9ca314ea783084c0e040970   
2261   fd0dcf4488bd367fb7c516ad27135d64  83f280a4e3c23c5a9ba16aa38de7ff30   
37504  fd7134a72d3b3725940ac1063df7bd02  045570b1bbf635feb489741de1665e2b   
44376  fd79684012b83e3cb859ceede1c67e2c  416e692b55f5313dacf02dcb1740becc   
11049  fdac6a4dd57934d8b9a90e2a8d9182fe  7797fc8c83d53672b870883be2865a99   
21959  fde48dce711f31acbcb5fc73ed9bca99  1a90bb57654d3967ad597d3f1f58fc3f   
47763  fe1408e734fc3805a79c5446473d94d6  3ec02e6e7c1f30b199ab6831ec018742   
45741  fe24590481603c7dbe5517b6d1d612b8  2a649ee675803cdd86b59a26e612150f   
4902   fe2b27ed50963c35b1e40250c4b082e2  6a5d5def3ff5340b8b45eab3c1b8a073   
40297  fe66505c602133d3b642aaffa65fbf6a  9d08cb1645ac3c95b628c5c90342f725   
36872  fea05900f67f3d3789572b87ce69ab16  f5c83eb87f183083a4957555b05c4ead   
3071   feadd1cf5f28303f9872176e04

In [39]:
df_rst.to_csv('./submition/0430.tsv', sep='\t', index=None)